## Preamble

Hi Acerola!

I am really happy this file has reached you. 

If you wish to ask further questions, poke at my method or require additional explanation, feel free to reach me in Discord (`@ktnlvr`) or by email `artur.roos@ktnlvr.dev`/`artur.roos.artur@gmail.com`.

## Introduction

We can view an AABB of set $S$ as a pair of vectors $v$ and $u$, such that $v_x = \sup \{ p_x | p_x \in S\}$, $v_y = \sup \{p_y | p_y \in S\}$, $u_x = \inf \{ p_x | p_x \in S\}$, $u_y = \inf \{p_y | p_y \in S\}$.

## Assumptions

By virtue of my position, I do not have time to analytically show that the following statements are true, so I will do my best to state my assumptions as is and follow up with a full proof later (mayhaps). Just wanted to get my hat into the ring with a statement that it is, in fact, possible.


### Part 1: Scaling, Translating
1. Come to terms with the fact that any linear transformation is a composition of Scaling, Rotating and Translating (refer to [this stackexchange](https://math.stackexchange.com/questions/237369/given-this-transformation-matrix-how-do-i-decompose-it-into-translation-rotati)).
2. All vectors $v$ that are inside an AABB will stay inside after *any* scaling.
3. When vectors inside an AABB are translated, it is translated along with them.
4. A rotation does not preserve a bounding box. If you imagine two vectors (0, 0) and (1, 1), the bounding box will have them as minimal and maximal vectors respectively. After a 45 degree rotation, the bounding box will no longer contain the vector (1, 1).
5. From [2, 3] it follows that for scaling and translating it is sufficient for a system with scaling and translating to only calculate the bounding box! I.e., for the Sierpinsky Triangle it is enough to recalculate the bounds of the AABB.

### Part 2: Rotation
5. From [3], this can't be enough for all of them. We can take the Convex Hull using a gift-wrapping algorithm (for 2D) or a Delaunay Triangulation with the Bowyer–Watson algorithm (for 3D). By definition, it is always the outermost points of a set, so the bounding box generated from only the outermost complex hull is representative.
6. Every time a linear transformation is applied, a transformed point is confined to the tranformed hull. Imagine a hull. Without loss of generality, we may translate this hull however we want accordingly to [2]. For every point $p$ inside the hull has to exist a point $p'$ on the hull, such that it's the closest in some direction. Both points have to lie on a ray that starts at the origin.Trivially, the point $p'$ is always more impacted by any transformation more than $p$, by virtue of having larger components along their common line. Hence, it contains sufficient information for all the other points along the ray that are inside the hull. 
7. All of the above means that the convex hull from [5] covers scaling [2], translating [3] and rotating [4, 6], which is sufficient [1]. We can only observe the motion of the points in the convex hull, which is significantly cheaper.

The overall complexity comes from the convex hull, O(N^2). However, all in all very few points need to be maintained. An approximation can be used too!

## Rigorous Proof (unfinished)

Any affine 3x3 matrix can be decomposed into rotation 2x2, scaling 2x2 and translation 3x3.

$$A = TSR\,M$$

Where $T$ is the translation, $S$ is the scaling and $R$ is a rotation respectively.

We can view each matrix $A$ as the following:
$$A = \left\lceil\begin{matrix}s_x\cos \theta & -s_x\sin \theta & t_x\\
s_y\sin \theta & s_y\cos \theta & t_y\\ 0 & 0 & 1 \end{matrix}\right\rceil$$

That means that understanding the influence of these transformations on an AABB is sufficient to construct one.

to be continued...

## Nota Bene

We can use the fact that the attractor converges to stop the iteration early. It will depend on the rate of convergence of a specific IFS, but we can use a general `EPS = 1e-12`, which should be enough for all intents and purposes.

In [1]:
%pip install sympy numpy nbformat plotly scikit-learn

Note: you may need to restart the kernel to use updated packages.


In [2]:
import numpy as np
import plotly.express as px
from scipy.spatial import ConvexHull

In [3]:
def S(s_x, s_y=None):
    s_y = s_y or s_x
    return np.array([[s_x, 0, 0], [0, s_y, 0], [0, 0, 1]])


def R(theta):
    return np.array(
        [
            [np.cos(theta), -np.sin(theta), 0],
            [np.sin(theta), np.cos(theta), 0],
            [0, 0, 1],
        ]
    )


def T(x, y):
    return np.array([[1, 0, x], [0, 1, y], [0, 0, 1]])


def M4(x_00, x_01, x_10, x_11):
    return np.array([[x_00, x_01, 0], [x_10, x_11, 0], [0, 0, 1]])


def affine_serpinski():
    f1 = np.matmul(T(0, 0.36), S(0.5))
    f2 = np.matmul(T(-0.5, -0.5), S(0.5))
    f3 = np.matmul(T(0.5, -0.5), S(0.5))
    return [f1, f2, f3]


def affine_fern():
    f1 = M4(0, 0, 0, 0.16)
    f2 = np.matmul(T(0, 1.6), M4(0.85, 0.04, -0.04, 0.85))
    f3 = np.matmul(T(0, 1.6), M4(0.2, -0.26, 0.23, 0.22))
    f4 = np.matmul(T(0, 0.44), M4(-0.15, 0.28, 0.26, 0.24))
    return [f1, f2, f3, f4]


As = affine_fern()

In [4]:
origin = np.array([0, 0, 1])
generations = 10
MAX_GENERATIONS = 8  # limit the generations for the "brute-force"

In [7]:
# for 3 dimensions use a Delanau Triangulation, it is identical to a convex hull. 
def compute_convex_hull():
    hull = np.array([origin])
    for i in range(min(generations, MAX_GENERATIONS)):
        points = []
        for p in hull:
            for A in As:
                try:
                    points.append(np.matmul(A, p))
                except:
                    display(A, p)
                    raise
        hull = list(map(lambda p: p[:2], points))
        if i > 3: # convex hull does not exist if all the values are on the same coordinate
            hull = ConvexHull(points, qhull_options="QJ").points
        hull = np.array(list(map(lambda p: [p[0], p[1], 1], hull)))
    return hull

def convex_hull_to_aabb(hull):
    mi = np.array([np.inf, np.inf])
    ma = -mi
    for p in hull:
        mi[0] = min(mi[0], p[0])
        mi[1] = min(mi[1], p[1])
        ma[0] = max(ma[0], p[0])
        ma[1] = max(ma[1], p[1])
    return np.array([mi, ma])

def compute_aabb():
    return convex_hull_to_aabb(compute_convex_hull())

AABB = compute_aabb()
AABB

array([[-1.70899301,  0.        ],
       [ 1.89300453,  7.68044912]])

In [11]:
# The diagonal line goes from the minimal to the maximal vector

def generate_bruteforce():
    points = [origin]
    for _ in range(min(generations, MAX_GENERATIONS)):
        new_points = []
        for p in points:
            for A in As:
                new_points.append(np.matmul(A, p))
        points = new_points
    points = np.array(points)
    px.scatter(x=points[:, 0], y=points[:, 1]).add_scatter(x=AABB[:, 0], y=AABB[:, 1]).add_shape(x0=AABB[0][0], y0=AABB[0][1], x1=AABB[1][0], y1=AABB[1][1],
        line=dict(
            color="red",
            width=2,
        ),).show()

generate_bruteforce()

by Artur Roos for Acerola. 2024-12-03

No particular license, just be nice and don't make it into a paper without me pls